In [1]:
import requests
from bs4 import BeautifulSoup
from fake_useragent import UserAgent
import time
import random
import json

In [2]:
ua = UserAgent()
listUserAgent = [ua.chrome, ua.ie, ua.msie, ua.opera, ua.google, ua['google chrome'], ua['Internet Explorer'], ua.firefox, ua.ff, ua.safari]

## I. GET THE LINK BASE ON PLACES

In [3]:
def get_all_place_from_side_bar(url):
    pageToGetPlaceHref = requests.get(url)
    soupToGetPlaceHref = BeautifulSoup(pageToGetPlaceHref.content, 'html.parser')
    aHrefSideBarList = soupToGetPlaceHref.select(".tourListSideBar a")   
    linkToGetPlace = []
    for aTag in aHrefSideBarList:
        linkToGetPlace.append(('https://www.ivivu.com'+aTag['href']).strip())
    return linkToGetPlace

In [4]:
URL = "https://www.ivivu.com/du-lich/tour-ha-noi?date=2020-12-02&from=h%e1%bb%93-ch%c3%ad-minh"
linkToGetPlace = get_all_place_from_side_bar(URL)

## II. GET THE DATA USING REQUESTS WITH FAKE AGENTS + TIMEOUT

In [5]:
def get_tour_detail_dict_from_url(url, ua):
    time.sleep(1)
    page = requests.get(url, ua)
    soup = BeautifulSoup(page.content, 'html.parser')
    scrape_content = soup.find_all('div', class_="tourHeaderContainer")[0]
    scrape_tour_id = ""
    scrape_background_img = ""
    try:
        scrape_bkground_el = soup.find('div', class_="tourHeaderCover2")
        scrape_tour_id = soup.find('b', class_="vcolor-info").getText()
        scrape_background_img = scrape_bkground_el['style']
    except:
        scrape_background_img = str(scrape_bkground_el)
    resultDict = {'id': scrape_tour_id, 'backgroundImg': scrape_background_img, 'content': scrape_content}
    
    return resultDict

In [6]:
# Test Get Tour Details of 1 Link
res = get_tour_detail_dict_from_url('https://www.ivivu.com/du-lich/tour-ta-dung-2n2d-bao-loc-dambri-linh-quy-lua-trai-nui-rung-bbq-thit-nuong/1237', ua.chrome)

In [8]:
def get_tour_detail_from_list(divTag, listUserAgent, lenListUA):
    randomUA = listUserAgent[random.randint(0, lenListUA)]
    tourDetailURL = 'https://www.ivivu.com'+divTag.find_all('a', class_='linkDetail')[0]['href']
    imgTourSrc = divTag.find_all('img', class_='visible-xs')[0]['data-src']
    tourTitle = divTag.find_all('a', class_='linkDetail')[1].get_text().strip()
    tourPros = divTag.find_all('ul', class_='tourListPros')[0]
    tourPrice = divTag.find_all('div', class_='tourItemContentPrice')[0]
    tourProsAndExtra = divTag.find_all('div', class_='v-margin-top-10')[0]
    #tourDestinations = "" if len(divTag.find_all('div', class_='cardItemPriceDivOuter')) == 0 else divTag.find_all('div', class_='cardItemPriceDivOuter')[0]
    detailDict = get_tour_detail_dict_from_url(tourDetailURL, randomUA)
    tourDetailDict = {'tourId': detailDict['id']
                      , 'tourUrl': tourDetailURL
                      , 'tourImgSrc': imgTourSrc
                      , 'tourTitle': tourTitle
                      , 'tourPros': tourPros
                      , 'tourPrice': tourPrice
                      , 'tourProsAndExtra': tourProsAndExtra
                      #, 'tourDestinations': tourDestinations
                      , 'tourDetail': detailDict
                     }
    return tourDetailDict

In [9]:
def get_tour_detail_links_from_url(url, listUserAgent):
    lenListUA = len(listUserAgent)-1
    header = listUserAgent[random.randint(0, lenListUA)]   
    detailList = []
    page = requests.get(url, header)
    soupToGetTourHref = BeautifulSoup(page.content, 'html.parser')
    divTourList = soupToGetTourHref.find_all('div', class_='tourItem')
    for divTag in divTourList:
        tourDetailDict = get_tour_detail_from_list(divTag, listUserAgent, lenListUA)
        detailList.append(tourDetailDict)
    return detailList

In [10]:
# Test above func on the tour-han-quoc (3 items only)
linkDetails = get_tour_detail_links_from_url('https://www.ivivu.com/du-lich/tour-quy-nhon', listUserAgent)

In [11]:
linkDetails

[{'tourId': 'TO1188',
  'tourUrl': 'https://www.ivivu.com/du-lich/tour-mien-trung-3n4d-kham-pha-quy-nhon-phu-yen-tau-lua-tet/1188',
  'tourImgSrc': '//cdn2.ivivu.com/2016/02/18/17/ganh-da-dia-450x265.jpg',
  'tourTitle': 'Tour Miền Trung 3N4D: Khám Phá Quy Nhơn - Phú Yên ( Tàu Lửa) Tết',
  'tourPros': <ul class="tourListPros list-inline v-margin-top-10">
  <li>Cendeluxe tiêu chuẩn 5 sao</li>
  <li>Đảo Kỳ Co</li>
  <li>Gành Đá Dĩa</li>
  <li>Bãi Xếp</li>
  <li>Mũi Điện Đại Lãnh</li>
  </ul>,
  'tourPrice': <div class="col-xs-12 col-sm-4 col-md-4 col-lg-4 tourItemContentPrice text-right">
  <span class="tourItemDateTime">Khởi hành: 24-12-2020</span><br/>
  <span class="tourItemPrice">3.260.000<span class="tourItemCurrency"> VND</span></span><br/>
  <span class="tourItemPricePerGuest">*Áp dụng nhóm 2 khách</span><br/>
  <div class="tourBooking24H hidden" data-id="1188">0 khách đặt trong 24h qua</div>
  <br class="hidden-xs"/>
  </div>,
  'tourProsAndExtra': <div class="row v-margin-top-10

In [12]:
def create_tour_detail_dict_from_place_urls(urlList, listUserAgent):
    dictToDetail = {}
    for urlLink in urlList:
        time.sleep(1)
        linkDetailList = get_tour_detail_links_from_url(urlLink, listUserAgent)
        dictToDetail[urlLink] = linkDetailList
    return dictToDetail

In [13]:
detailDict = create_tour_detail_dict_from_place_urls(linkToGetPlace, listUserAgent)

In [41]:
detailDict

{'https://www.ivivu.com/du-lich/tour-chau-au': [{'tourUrl': 'https://www.ivivu.com/du-lich/dich-vu-visa-my/1225',
   'tourImgSrc': 'https://cdn2.ivivu.com/2020/03/04/09/ivivu-visa-my-2-450x265.gif',
   'tourTitle': 'Dịch vụ Visa Mỹ',
   'tourPros': <ul class="tourListPros list-inline v-margin-top-10">
   </ul>,
   'tourPrice': <div class="col-xs-12 col-sm-4 col-md-4 col-lg-4 tourItemContentPrice text-right">
   <span class="tourItemFull">Hết chỗ</span><br/>
   <br class="hidden-xs"/>
   </div>,
   'tourProsAndExtra': <div class="row v-margin-top-10">
   <div class="col-xs-12 col-sm-8 col-md-8 col-lg-8">
   <span class="tourItemName">
   <a class="linkDetail" data-datedepart="12/1/2020 12:23:59 PM" href="/du-lich/dich-vu-visa-my/1225" target="_blank">
                                                                                           Dịch vụ Visa Mỹ
                                                                                       </a>
   </span><br/>
   <div class="v-margin-

In [14]:
str(detailDict['https://www.ivivu.com/du-lich/tour-chau-au'][0]['tourDetail']['content'])

'<div class="col-xs-12 no-padding tourHeaderContainer v-margin-bottom-30">\n<div class="col-xs-12 no-padding padding-mobile">\n<div class="tourHeaderCover2" style="background-image: url(\'//cdn2.ivivu.com/2020/03/04/09/ivivu-visa-my-750x390.gif\');">\n<div class="ribbonContainerOuter">\n<div class="ribbonContainerInner">\n<span class="v-ribbon"><h1>Tour bán chạy <label class="price-hot"></label></h1></span>\n</div>\n</div>\n<div class="@*visible-xs-inline*@ hidden">\n<div class="col-xs-12 tourHeaderBackgroundTrans">\n<h1> <span class="vcolor-white no-margin title"><b>Dịch vụ Visa Mỹ</b></span></h1>\n</div>\n</div>\n</div>\n</div>\n<div class="col-xs-12">\n<div class="row tourHeaderInfo belowCover">\n<div class="col-xs-12">\n<span class="v-margin-right-30"><i class="glyphicon glyphicon-map-marker"></i>Hồ Chí Minh</span><br class="visible-xs"/>\n<span class="v-margin-right-30 timeName" data-timename="Trong Ngày"><i class="glyphicon glyphicon-time"></i>Trong Ngày</span>\n<span class="v-ma

In [15]:
for k,v in detailDict.items():
    for tour in v:
        tour['tourPrice'] = str(tour['tourPrice'])
        tour['tourPros'] = str(tour['tourPros'])
        tour['tourProsAndExtra'] = str(tour['tourProsAndExtra'])
        tour['tourDetail']['content'] = str(tour['tourDetail']['content'])

## III. DUMP DICT TO JSON FILE

In [16]:
def create_json_file_from_dict(convertDict, fileName):
    app_json = json.dumps(convertDict)
    out_file = open(fileName+'.json', "w") 
    json.dump(convertDict, out_file, indent = 6)    

In [17]:
create_json_file_from_dict(detailDict, "scrape_ivivu_new")

## IV. ACCESS THE JSON FILE AND UPDATE NEW

In [18]:
json_file = open('scrape_ivivu.json',)

In [48]:
data_dict = json.load(json_file)

In [49]:
json_file.close()